<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#XR-Generator" data-toc-modified-id="XR-Generator-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>XR Generator</a></span></li></ul></div>

In [ ]:
%matplotlib inline

In [ ]:
from pathlib import Path
import numpy as np
import pickle as pkl
import pandas as pd
import xarray as xr
import SimpleITK as sitk

import holoviews as hv
from holoviews import opts
import hvplot.pandas
hv.extension('bokeh')
import matplotlib.pyplot as plt
plt.rcParams['figure.figsize'] = (10,8)

from mre.plotting import patient_series_viewer, patient_reg_comparison, xr_viewer_v2
from mre.preprocessing import MRIImage
from mre.registration_v2 import RegPatient, Register, GroupRegister
from mre.mre_datasets import MREtoXr

%load_ext autoreload
%autoreload 2
%opts Image [tools=['hover'] height=500 width=500 yaxis=None xaxis=None] (cmap='viridis')

In [ ]:
data_dir = Path('/pghbio/dbmi/batmanlab/Data/MRE/MRE_DICOM_7-31-19/NIFTI')
data_dir2 = Path('/pghbio/dbmi/batmanlab/Data/MRE/MRE_DICOM_9-12-19/NIFTI')

In [ ]:
ls /pghbio/dbmi/batmanlab/Data/CombinedHealthyAbdominalOrganSegmentation/MR_data_batch1/

In [5]:
df = pd.read_pickle('/pghbio/dbmi/batmanlab/bpollack/predictElasticity/data/MRE/dicom_scrape.p')
df = df[~df.index.duplicated(keep='first')]

In [6]:
#moving_atlas = RegPatient('15', atlas_dir)
#test_patient = RegPatient('0006', data_dir)

In [7]:
test_patient.images

{'t1_pos_fat': <SimpleITK.SimpleITK.Image; proxy of <Swig Object of type 'std::vector< itk::simple::Image >::value_type *' at 0x7fb8b1acbba0> >,
 'mre': <SimpleITK.SimpleITK.Image; proxy of <Swig Object of type 'std::vector< itk::simple::Image >::value_type *' at 0x7fb8b1acbc00> >,
 't1_pre_fat': <SimpleITK.SimpleITK.Image; proxy of <Swig Object of type 'std::vector< itk::simple::Image >::value_type *' at 0x7fb8b1acbcc0> >,
 'mre_raw': <SimpleITK.SimpleITK.Image; proxy of <Swig Object of type 'std::vector< itk::simple::Image >::value_type *' at 0x7fb8b1acbc30> >,
 't1_pre_water': <SimpleITK.SimpleITK.Image; proxy of <Swig Object of type 'std::vector< itk::simple::Image >::value_type *' at 0x7fde516c3c60> >,
 't1_pre_in': <SimpleITK.SimpleITK.Image; proxy of <Swig Object of type 'std::vector< itk::simple::Image >::value_type *' at 0x7fde516c3ab0> >,
 'mre_mask': <SimpleITK.SimpleITK.Image; proxy of <Swig Object of type 'std::vector< itk::simple::Image >::value_type *' at 0x7fde516c3a80>

In [17]:
patient_series_viewer(data_dir.parent, 'DICOMA/PA4/ST0', img_type='DICOM')

/pghbio/dbmi/batmanlab/Data/MRE/MRE_DICOM_7-31-19/DICOMA/PA4/ST0/SE0
direction (1.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0)
origin (-209.17999267578125, -239.17999267578125, -16.0)
(21, 256, 256)
:Dataset   [xSE0 3Plane Loc End Expiration 2060,ySE0 3Plane Loc End Expiration 2060,zSE0 3Plane Loc End Expiration 2060]   (MRISE0 3Plane Loc End Expiration 2060)
/pghbio/dbmi/batmanlab/Data/MRE/MRE_DICOM_7-31-19/DICOMA/PA4/ST0/SE1
direction (1.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0)
origin (-221.64100646972656, -249.14100646972656, 111.19999694824219)
(21, 256, 256)
:Dataset   [xSE1 3Plane Loc End Expiration 2060,ySE1 3Plane Loc End Expiration 2060,zSE1 3Plane Loc End Expiration 2060]   (MRISE1 3Plane Loc End Expiration 2060)
/pghbio/dbmi/batmanlab/Data/MRE/MRE_DICOM_7-31-19/DICOMA/PA4/ST0/SE2
direction (1.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0)
origin (-201.44500732421875, -249.17999267578125, 158.20700073242188)
(32, 256, 256)
:Dataset   [xSE2 Ax MR Touch End Expiration 2060,ySE2 Ax 

:Layout
   .DynamicMap.I                                                                     :DynamicMap   [zSE0 3Plane Loc End Expiration 2060]
      :Image   [xSE0 3Plane Loc End Expiration 2060,ySE0 3Plane Loc End Expiration 2060]   (MRISE0 3Plane Loc End Expiration 2060)
   .DynamicMap.II                                                                    :DynamicMap   [zSE1 3Plane Loc End Expiration 2060]
      :Image   [xSE1 3Plane Loc End Expiration 2060,ySE1 3Plane Loc End Expiration 2060]   (MRISE1 3Plane Loc End Expiration 2060)
   .DynamicMap.III                                                                   :DynamicMap   [zSE2 Ax MR Touch End Expiration 2060]
      :Image   [xSE2 Ax MR Touch End Expiration 2060,ySE2 Ax MR Touch End Expiration 2060]   (MRISE2 Ax MR Touch End Expiration 2060)
   .DynamicMap.IV                                                                    :DynamicMap   [zSE3 Cor T2 SSFSE BH 2060]
      :Image   [xSE3 Cor T2 SSFSE BH 2060,ySE3 Cor T2 SSFSE BH 2060]   (MRISE3 Cor T2 SSFSE BH 2060)
   .DynamicMap.V                                                                     :DynamicMap   [zSE4 AXIAL T2 SSFSE BH 2060]
      :Image   [xSE4 AXIAL T2 SSFSE BH 2060,ySE4 AXIAL T2 SSFSE BH 2060]   (MRISE4 AXIAL T2 SSFSE BH 2060)
   .DynamicMap.VI                                                                    :DynamicMap   [zSE5 Ax GRE 2060]
      :Image   [xSE5 Ax GRE 2060,ySE5 Ax GRE 2060]   (MRISE5 Ax GRE 2060)
   .DynamicMap.VII                                                                   :DynamicMap   [zSE6 WATER: Ax LAVA-Flex 2060]
      :Image   [xSE6 WATER: Ax LAVA-Flex 2060,ySE6 WATER: Ax LAVA-Flex 2060]   (MRISE6 WATER: Ax LAVA-Flex 2060)
   .DynamicMap.VIII                                                                  :DynamicMap   [zSE7 Screen Save 2060]
      :Image   [xSE7 Screen Save 2060,ySE7 Screen Save 2060]   (MRISE7 Screen Save 2060)
   .DynamicMap.IX                                                                    :DynamicMap   [zSE8 Elastogram + Mask (Gray) 2060]
      :Image   [xSE8 Elastogram + Mask (Gray) 2060,ySE8 Elastogram + Mask (Gray) 2060]   (MRISE8 Elastogram + Mask (Gray) 2060)
   .DynamicMap.X                                                                     :DynamicMap   [zSE9 Elastogram (Gray) 2060]
      :Image   [xSE9 Elastogram (Gray) 2060,ySE9 Elastogram (Gray) 2060]   (MRISE9 Elastogram (Gray) 2060)
   .Image.SE10_Elastogram_left_parenthesis_0_hyphen_minus_8K_right_parenthesis_2060  :Image   [x,y]   (z)
   .Image.SE11_Elastogram_left_parenthesis_0_hyphen_minus_20K_right_parenthesis_2060 :Image   [x,y]   (z)
   .Image.SE12_Wave_Images_2060                                                      :Image   [x,y]   (z)
   .DynamicMap.XI                                                                    :DynamicMap   [zSE13 FAT: Ax LAVA-Flex 2060]
      :Image   [xSE13 FAT: Ax LAVA-Flex 2060,ySE13 FAT: Ax LAVA-Flex 2060]   (MRISE13 FAT: Ax LAVA-Flex 2060)
   .DynamicMap.XII                                                                   :DynamicMap   [zSE14 InPhase: Ax LAVA-Flex 2060]
      :Image   [xSE14 InPhase: Ax LAVA-Flex 2060,ySE14 InPhase: Ax LAVA-Flex 2060]   (MRISE14 InPhase: Ax LAVA-Flex 2060)
   .DynamicMap.XIII                                                                  :DynamicMap   [zSE15 OutPhase: Ax LAVA-Flex 2060]
      :Image   [xSE15 OutPhase: Ax LAVA-Flex 2060,ySE15 OutPhase: Ax LAVA-Flex 2060]   (MRISE15 OutPhase: Ax LAVA-Flex 2060)

## XR Generator

In [ ]:
sequences = ['t1_pre_water', 't1_pre_out', 't2']

In [ ]:
xr_maker = MREtoXr(data_dir, sequences)
ds = xr_maker.load_xr()

In [ ]:
ds

In [ ]:
xr_viewer_v2(ds)

In [18]:
ds[['image_mri', 'mask_mri']].copy()

<xarray.Dataset>
Dimensions:    (mask_type: 2, sequence: 3, subject: 2, x: 256, y: 256, z_mri: 32)
Coordinates:
  * sequence   (sequence) <U12 't1_pre_water' 't1_pre_out' 't2'
  * subject    (subject) <U4 '0006' '0314'
  * x          (x) int64 0 1 2 3 4 5 6 7 8 ... 248 249 250 251 252 253 254 255
  * mask_type  (mask_type) <U5 'liver' 'mre'
  * z_mri      (z_mri) int64 0 1 2 3 4 5 6 7 8 9 ... 23 24 25 26 27 28 29 30 31
  * y          (y) int64 255 254 253 252 251 250 249 248 247 ... 7 6 5 4 3 2 1 0
Data variables:
    image_mri  (subject, sequence, x, y, z_mri) int16 69 89 110 132 ... 0 0 0 0
    mask_mri   (subject, mask_type, x, y, z_mri) int16 1 0 0 0 0 0 ... 0 0 0 0 0